# [Clustering4Ever](https://github.com/Clustering4Ever/Clustering4Ever) on [SparkNotebook](http://spark-notebook.io/) by [LIPN](https://lipn.univ-paris13.fr/) [A3](https://lipn.univ-paris13.fr/accueil/equipe/a3/) team

In [ ]:
import smile.plot._
import scala.io.Source
import scala.collection.{immutable, mutable, parallel, GenSeq}
import org.clustering4ever.scala.clustering.kcenters.{KMeans, KMeansArgs}
import org.clustering4ever.spark.clustering.kcenters.{KMeans => KMeansSpark, KMeansArgs => KMeansArgsSpark}
import org.clustering4ever.math.distances.scalar.{Euclidean, Cosine, Minkowski}
import org.clustering4ever.indices.{ExternalIndicesLocal, InternalIndicesLocal}
import org.clustering4ever.enums.NmiNormalizationNature._
import org.clustering4ever.enums.ExternalsIndices
import org.clustering4ever.enums.InternalsIndices
import org.clustering4ever.clustering.EasyVectorizationDistributed
import org.clustering4ever.util.ScalaCollectionImplicits._
import org.clustering4ever.clusterizables.EasyClusterizable
import org.clustering4ever.vectorizables.Vectorizable
import org.clustering4ever.vectors.ScalarVector
import org.clustering4ever.vectorizations.{EasyVectorizationLocal, VectorizationNature, Scalar, Default}
import org.clustering4ever.scala.clustering.rla.{RLAArgs, RLAArgsScalar, RLA, RLAScalar}
import org.clustering4ever.shapeless.{VMapping, VectorizationMapping}
import org.clustering4ever.clustering.chaining.{ClusteringChainingLocal, BigDataClusteringChaining, DistributedClusteringChaining}
import org.clustering4ever.clustering.{ClusteringInformationsLocal, EasyVectorizationDistributed}
import scala.collection.parallel
import scala.collection.parallel.mutable.ParArray
import org.clustering4ever.clustering.indices.ClustersIndicesAnalysisLocal

import smile.plot._
import scala.io.Source
import scala.collection.{immutable, mutable, parallel, GenSeq}
import org.clustering4ever.scala.clustering.kcenters.{KMeans, KMeansArgs}
import org.clustering4ever.spark.clustering.kcenters.{KMeans=>KMeansSpark, KMeansArgs=>KMeansArgsSpark}
import org.clustering4ever.math.distances.scalar.{Euclidean, Cosine, Minkowski}
import org.clustering4ever.indices.{ExternalIndicesLocal, InternalIndicesLocal}
import org.clustering4ever.enums.NmiNormalizationNature._
import org.clustering4ever.enums.ExternalsIndices
import org.clustering4ever.enums.InternalsIndices
import org.clustering4ever.clustering.EasyVectorizationDistributed
import org.clustering4ever.util.ScalaCollectionImplicits._
import org.clustering4ever.clusterizables.EasyClusterizable
import or...

In [ ]:
:sh wget -P /tmp/ http://www.clustering4ever.org/Datasets/Aggregation/aggregation.csv
:sh wget -P /tmp/ http://www.clustering4ever.org/Datasets/Aggregation/labels

--2019-01-17 23:12:51--  http://www.clustering4ever.org/Datasets/Aggregation/aggregation.csv
Resolving www.clustering4ever.org (www.clustering4ever.org)... 62.210.16.62
Connecting to www.clustering4ever.org (www.clustering4ever.org)|62.210.16.62|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 8063 (7.9K) [text/csv]
Saving to: ‘/tmp/aggregation.csv’

     0K .......                                               100% 1.34G=0s

2019-01-17 23:12:51 (1.34 GB/s) - ‘/tmp/aggregation.csv’ saved [8063/8063]

:sh: Scheme missing.
--2019-01-17 23:12:51--  http://wget/
Resolving wget (wget)... failed: Name or service not known.
wget: unable to resolve host address ‘wget’
--2019-01-17 23:12:51--  http://www.clustering4ever.org/Datasets/Aggregation/labels
Reusing existing connection to www.clustering4ever.org:80.
HTTP request sent, awaiting response... 200 OK
Length: 1576 (1.5K)
Saving to: ‘/tmp/labels’

     0K .                                                     100%  319

In [ ]:
val datasetSize = 100000
val dim = 10
val path = "/tmp/aggregation.csv"
val useAggregationDS = true

val rawData = if(useAggregationDS) Source.fromFile(path).getLines.map( x => mutable.ArrayBuffer(x.split(",").map(_.toDouble):_*) ).toBuffer
  else mutable.ArrayBuffer.fill(datasetSize)(mutable.ArrayBuffer.fill(dim)(scala.util.Random.nextDouble))
val groundTruePath = "/tmp/labels"

datasetSize: Int = 100000
dim: Int = 10
path: String = /tmp/aggregation.csv
useAggregationDS: Boolean = true
rawData: scala.collection.mutable.Buffer[scala.collection.mutable.ArrayBuffer[Double]] = ArrayBuffer(ArrayBuffer(15.55, 28.65), ArrayBuffer(14.9, 27.55), ArrayBuffer(14.45, 28.35), ArrayBuffer(14.15, 28.8), ArrayBuffer(13.75, 28.05), ArrayBuffer(13.35, 28.45), ArrayBuffer(13.0, 29.15), ArrayBuffer(13.45, 27.5), ArrayBuffer(13.6, 26.5), ArrayBuffer(12.8, 27.35), ArrayBuffer(12.4, 27.85), ArrayBuffer(12.3, 28.4), ArrayBuffer(12.2, 28.65), ArrayBuffer(13.4, 25.1), ArrayBuffer(12.95, 25.95), ArrayBuffer(12.9, 26.5), ArrayBuffer(11.85, 27.0), ArrayBuffer(11.35, 28.0), ArrayBuffer(11.15, 28.7), ArrayBuffer(11.25, 27.4), ArrayBuffer(10.75, 27.7), ArrayBuffer(10.5, 28.35), ArrayBuffer(9....

## Transform your dataset adequately 

In [ ]:
val data = rawData.zipWithIndex.toVector.map{ case (v, id) => EasyClusterizable(id.toLong, ScalarVector(v)) }
val rddData = sc.parallelize(data.seq, 10)

data: scala.collection.immutable.Vector[org.clustering4ever.clusterizables.EasyClusterizable[Long,org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]]]] = Vector(EasyClusterizable(0,Vectorizable(ScalarVector(ArrayBuffer(15.55, 28.65))),ScalarVector(ArrayBuffer(15.55, 28.65)),shapeless.HMap@6dd07060,Vector()), EasyClusterizable(1,Vectorizable(ScalarVector(ArrayBuffer(14.9, 27.55))),ScalarVector(ArrayBuffer(14.9, 27.55)),shapeless.HMap@450f2d15,Vector()), EasyClusterizable(2,Vectorizable(ScalarVector(ArrayBuffer(14.45, 28.35))),ScalarVector(ArrayBuffer(14.45, 28.35)),shapeless.HMap@72793405,Vector()), EasyClusterizable(3,Vectorizable(ScalarVector(ArrayBuffer(14.15, 28.8...

## Let's try two metrics

### For every metrics you have to precise the nature of your vector (List[Int], Vector[Double], mutable.ArrayBuffer[Int],...)

In [ ]:
val metric = Euclidean[mutable.ArrayBuffer[Double]](false)
val metric2 = Minkowski[mutable.ArrayBuffer[Double]](4)

metric: org.clustering4ever.math.distances.scalar.Euclidean[scala.collection.mutable.ArrayBuffer[Double]] = Euclidean distance without squared root applied
metric2: org.clustering4ever.math.distances.scalar.Minkowski[scala.collection.mutable.ArrayBuffer[Double]] = Minkowski(4,3)


## Easy instantiation the of various clustering chaining tool

In [ ]:
val cc = ClusteringChainingLocal(data)
val ccrdd = BigDataClusteringChaining(rddData)
val ccsmallOnDistributedSystem = DistributedClusteringChaining(sc, data)
val firstVecto = cc.currentVectorization
val firstVectoCopy2 = ccsmallOnDistributedSystem.currentVectorization

cc: org.clustering4ever.clustering.chaining.ClusteringChainingLocal[Long,org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.clusterizables.EasyClusterizable,org.clustering4ever.vectorizations.EasyVectorizationLocal,scala.collection.immutable.Vector] = ClusteringChainingLocal(Vector(EasyClusterizable(0,Vectorizable(ScalarVector(ArrayBuffer(15.55, 28.65))),ScalarVector(ArrayBuffer(15.55, 28.65)),shapeless.HMap@6dd07060,Vector()), EasyClusterizable(1,Vectorizable(ScalarVector(ArrayBuffer(14.9, 27.55))),ScalarVector(ArrayBuffer(14.9, 27.55)),shapeless.HMap@450f2d15,Vector()), EasyClusterizable(2,Vectorizable(ScalarVector(ArrayBuffer(14.45, 28.35))),S...

## Full initialization

More option are available cf api doc

In [ ]:
def newVecto(v: ScalarVector[mutable.ArrayBuffer[Double]]) = new ScalarVector(v.vector)
val vectorizationL = EasyVectorizationLocal[ScalarVector[mutable.ArrayBuffer[Double]], ScalarVector[mutable.ArrayBuffer[Double]]](1, Some(identity _))
val vectorizationD = EasyVectorizationDistributed(1, Some(newVecto _))

val cc_ = ClusteringChainingLocal(data, 1, vectorizationL)
val ccrdd_ = BigDataClusteringChaining(rddData, 2, vectorizationD)
val ccsmallOnDistributedSystem_ = DistributedClusteringChaining(sc, data, 3, vectorizationL)

newVecto: (v: org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]])org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]]
vectorizationL: org.clustering4ever.vectorizations.EasyVectorizationLocal[org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]]] = EasyVectorizationLocal(1,Some(<function1>),Set(),Vector())
vectorizationD: org.clustering4ever.clustering.EasyVectorizationDistributed[org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]]] = EasyVectorizationDistributed(1,Some(<function1...

## Two ways to prepare algorithm to test
### The painfull one

In [ ]:
val rlaArgs = RLAArgsScalar(metric, 2D)
val kMeansArgs = KMeansArgs(2, metric, 0.0001, 50)
val kMeansArgsSpark = KMeansArgsSpark(2, metric, 0.0001, 50)
val kMeans = KMeans[
    Long,
    ScalarVector[mutable.ArrayBuffer[Double]],
    mutable.ArrayBuffer[Double],
    EasyClusterizable,
    Euclidean,
    immutable.Vector
](kMeansArgs)
val rla = RLAScalar[
    Long,
    ScalarVector[mutable.ArrayBuffer[Double]],
    mutable.ArrayBuffer[Double],
    EasyClusterizable,
    Euclidean,
    immutable.Vector
](rlaArgs)

val kMeansVariousK = (3 to 9).map{ i =>
  KMeans[
    Long,
    ScalarVector[mutable.ArrayBuffer[Double]],
    mutable.ArrayBuffer[Double],
    EasyClusterizable,
    Euclidean,
    immutable.Vector
  ](
    KMeansArgs(i, metric, 0.0001, 50)
  )
}

val kMeansVariousKSpark = (3 to 9).map{ i =>
  KMeansSpark[
    Long,
    ScalarVector[mutable.ArrayBuffer[Double]],
    mutable.ArrayBuffer[Double],
    EasyClusterizable,
    Euclidean
  ](
    KMeansArgsSpark(i, metric, 0.0001, 50)
  )
}

val algosObtainedPainfully = Seq(kMeans, rla) ++ kMeansVariousK
val algosObtainedSemiEffortlesslySpark = kMeansVariousKSpark :+ kMeansArgsSpark.obtainAlgorithm(rddData)

rlaArgs: org.clustering4ever.scala.clustering.rla.RLAArgsScalar[scala.collection.mutable.ArrayBuffer[Double],org.clustering4ever.math.distances.scalar.Euclidean] = RLAArgsScalar(Euclidean distance without squared root applied,2.0)
kMeansArgs: org.clustering4ever.scala.clustering.kcenters.KMeansArgs[scala.collection.mutable.ArrayBuffer[Double],org.clustering4ever.math.distances.scalar.Euclidean] = KMeansArgs(2,Euclidean distance without squared root applied,1.0E-4,50,Map())
kMeansArgsSpark: org.clustering4ever.spark.clustering.kcenters.KMeansArgs[scala.collection.mutable.ArrayBuffer[Double],org.clustering4ever.math.distances.scalar.Euclidean] = KMeansArgs(2,Euclidean distance without squared root applied,1.0E-4,50,StorageLevel(memory, deserialized, 1 replicas),Map())
kMeans: org.clusteri...

## Easily using right methods

In [ ]:
val kmeansArgsCombinations = KMeans.generateAnyArgumentsCombination(
  (4 until 100), Seq(metric, metric2), Seq(5D), Seq(50, 100, 200), Seq(mutable.HashMap.empty[Int, ScalarVector[mutable.ArrayBuffer[Double]]])
)

val othersKmeansArgsCombinations = (23 to 30).map( i => KMeansArgs(i, metric, 0.0001, 50) )

val kmeansAlgos = kmeansArgsCombinations.map(_.obtainAlgorithm(data)).toBuffer
val others = othersKmeansArgsCombinations.map(_.obtainAlgorithm(data)).toSeq

kmeansArgsCombinations: Seq[org.clustering4ever.scala.clustering.kcenters.KMeansArgs[scala.collection.mutable.ArrayBuffer[Double],org.clustering4ever.math.distances.ContinuousDistance]] = Vector(KMeansArgs(4,Euclidean distance without squared root applied,5.0,50,Map()), KMeansArgs(4,Euclidean distance without squared root applied,5.0,100,Map()), KMeansArgs(4,Euclidean distance without squared root applied,5.0,200,Map()), KMeansArgs(4,Minkowski(4,3),5.0,50,Map()), KMeansArgs(4,Minkowski(4,3),5.0,100,Map()), KMeansArgs(4,Minkowski(4,3),5.0,200,Map()), KMeansArgs(5,Euclidean distance without squared root applied,5.0,50,Map()), KMeansArgs(5,Euclidean distance without squared root applied,5.0,100,Map()), KMeansArgs(5,Euclidean distance without squared root applied,5.0,200,Map()), KMeansArgs(...

## Local Algorithms launched multiple algorithms PARALLELY on local machine

In [ ]:
val t0 = System.currentTimeMillis
val cc2 = cc.runAlgorithms(kmeansAlgos:_*)
val t1 = System.currentTimeMillis
val cc3 = cc2.runAlgorithms(others:_*)
val t2 = System.currentTimeMillis
(t2 - t0) / 1000000D

t0: Long = 1547767009874
cc2: cc.Self[org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.vectorizations.EasyVectorizationLocal] = ClusteringChainingLocal(Vector(EasyClusterizable(0,Vectorizable(ScalarVector(ArrayBuffer(15.55, 28.65))),ScalarVector(ArrayBuffer(15.55, 28.65)),shapeless.HMap@6dd07060,Vector(3, 3, 2, 2, 0, 0, 2, 4, 0, 1, 4, 0, 5, 5, 1, 0, 2, 0, 0, 4, 5, 4, 6, 4, 5, 4, 5, 0, 4, 4, 4, 4, 4, 1, 7, 5, 3, 2, 5, 8, 8, 2, 2, 2, 0, 4, 7, 1, 0, 10, 3, 5, 11, 10, 4, 6, 11, 3, 2, 4, 1, 7, 1, 3, 4, 0, 6, 8, 5, 12, 10, 2, 15, 0, 9, 9, 0, 13, 8, 16, 15, 0, 6, 9, 15, 5, 14, 17, 0, 13, 13, 10, 9, 12, 10, 9, 13, 14, 13, 18, 10, 15, 0, 9, 18, 12, 8, 2, 11, 6, 21, 19, 7, 18, 10, 13, 0, 17, 1, 0, 17, 13, 16, 2, 5, 7, 12, 10, 21, 14, 15, 7...

0.018962

## Extract every clustering informations concerning a specific vectorization

In [ ]:
kmeansAlgos.size
cc3.currentVectorization.clusteringNumbers.size

val ClusteringInformationsLocal(infos, _ , _) = cc3.clusteringInformations.get(firstVecto.vectorizationID)(firstVecto.getInformationMapping(Some(data))).get

infos.toList.sortBy(_._1)

infos: scala.collection.immutable.HashSet[(org.clustering4ever.types.ClusteringInformationTypes.GlobalClusteringRunNumber, org.clustering4ever.vectorizations.EasyVectorizationLocal[org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]]], org.clustering4ever.clustering.ClusteringArgsLocal[org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]]], org.clustering4ever.clustering.ClusteringModelLocal[Long,org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.clusterizables.EasyClusterizable,scala.collection...

## Distributed Algorithms launch sequentially on a distributed system 

In [ ]:
val t0 = System.currentTimeMillis
val ccrdd2 = ccrdd.runAlgorithms(algosObtainedSemiEffortlesslySpark:_*)
val t1 = System.currentTimeMillis
(t1 - t0) / 1000000D

t0: Long = 1547767031472
ccrdd2: ccrdd.Self[org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.clustering.EasyVectorizationDistributed] = BigDataClusteringChaining(MapPartitionsRDD[1807] at map at BigDataClusteringChaining.scala:77,1419758185,EasyVectorizationDistributed(0,None,Set(0, 5, 1, 6, 2, 7, 3, 4),Vector()),shapeless.HMap@24546fb6)
t1: Long = 1547767038808
res54: Double = 0.007336


0.007336

In [ ]:
ccrdd2.data.first.clusterIDs

res56: scala.collection.immutable.Vector[Int] = Vector(2, 2, 2, 3, 4, 4, 7, 0)


entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total

## Local Algorithms launched parallely on a distributed system

In [ ]:
val t0 = System.currentTimeMillis
val ccsmallOnDistributedSystem2 = ccsmallOnDistributedSystem.runAlgorithms(10, kmeansAlgos:_*)
val t1 = System.currentTimeMillis
(t1 - t0) / 1000000D

0.030813

t0: Long = 1547767040317
ccsmallOnDistributedSystem2: ccsmallOnDistributedSystem.Self[org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.vectorizations.EasyVectorizationLocal] = DistributedClusteringChaining(org.apache.spark.SparkContext@29b2b214,Vector(EasyClusterizable(0,Vectorizable(ScalarVector(ArrayBuffer(15.55, 28.65))),ScalarVector(ArrayBuffer(15.55, 28.65)),shapeless.HMap@1c247f90,Vector(1, 0, 2, 0, 0, 1, 2, 2, 4, 4, 0, 2, 5, 1, 5, 4, 1, 4, 4, 4, 0, 3, 0, 5, 1, 1, 2, 6, 3, 1, 5, 5, 3, 4, 2, 4, 5, 6, 4, 3, 2, 9, 1, 5, 1, 9, 3, 5, 1, 7, 11, 9, 10, 2, 0, 2, 11, 9, 7, 7, 10, 11, 10, 10, 12, 2, 3, 10, 5, 6, 6, 14, 4, 11, 13, 12, 0, 7, 2, 9, 6, 6, 5, 12, 10, 16, 10, 14, 4, 15, 9, 18, 2, 18, 16, 15, 1, 0, 12, 1, 5, 17, 14, 13, 17,...

0.029524

In [ ]:
ccsmallOnDistributedSystem2.data.head.clusterIDs.size

576

res60: Int = 576


576

## Each run release a new clustering chaining object, with updated values

In [ ]:
val t0 = System.currentTimeMillis
val newCC = cc3.runAlgorithms(algosObtainedPainfully:_*)
val t1 = System.currentTimeMillis
(t1 - t0) / 10000000D

4.7E-6

t0: Long = 1547767071575
newCC: cc3.Self[org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.vectorizations.EasyVectorizationLocal] = ClusteringChainingLocal(Vector(EasyClusterizable(0,Vectorizable(ScalarVector(ArrayBuffer(15.55, 28.65))),ScalarVector(ArrayBuffer(15.55, 28.65)),shapeless.HMap@6dd07060,Vector(3, 3, 2, 2, 0, 0, 2, 4, 0, 1, 4, 0, 5, 5, 1, 0, 2, 0, 0, 4, 5, 4, 6, 4, 5, 4, 5, 0, 4, 4, 4, 4, 4, 1, 7, 5, 3, 2, 5, 8, 8, 2, 2, 2, 0, 4, 7, 1, 0, 10, 3, 5, 11, 10, 4, 6, 11, 3, 2, 4, 1, 7, 1, 3, 4, 0, 6, 8, 5, 12, 10, 2, 15, 0, 9, 9, 0, 13, 8, 16, 15, 0, 6, 9, 15, 5, 14, 17, 0, 13, 13, 10, 9, 12, 10, 9, 13, 14, 13, 18, 10, 15, 0, 9, 18, 12, 8, 2, 11, 6, 21, 19, 7, 18, 10, 13, 0, 17, 1, 0, 17, 13, 16, 2, 5, 7, 12, 10, 21, 14, 15...

3.2E-6

## Lets explore the clustering indices

In [ ]:
val indicesAnalysis = new ClustersIndicesAnalysisLocal(newCC.data)

indicesAnalysis: org.clustering4ever.clustering.indices.ClustersIndicesAnalysisLocal[Long,org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.clusterizables.EasyClusterizable,scala.collection.immutable.Vector] = ClustersIndicesAnalysisLocal(Vector(EasyClusterizable(0,Vectorizable(ScalarVector(ArrayBuffer(15.55, 28.65))),ScalarVector(ArrayBuffer(15.55, 28.65)),shapeless.HMap@6dd07060,Vector(3, 3, 2, 2, 0, 0, 2, 4, 0, 1, 4, 0, 5, 5, 1, 0, 2, 0, 0, 4, 5, 4, 6, 4, 5, 4, 5, 0, 4, 4, 4, 4, 4, 1, 7, 5, 3, 2, 5, 8, 8, 2, 2, 2, 0, 4, 7, 1, 0, 10, 3, 5, 11, 10, 4, 6, 11, 3, 2, 4, 1, 7, 1, 3, 4, 0, 6, 8, 5, 12, 10, 2, 15, 0, 9, 9, 0, 13, 8, 16, 15, 0, 6, 9, ...

In [ ]:
val internalIndices = InternalsIndices.values.toSeq.init
val extScores = indicesAnalysis.saveInternalsIndicesForEveryClusteringNumber(metric, internalIndices:_*)

val clusteringNumber = 5
// It is a tuple 3 as key, (MetricID, clusteringNumber, IndexEnum)
extScores.internalsIndicesByMetricClusteringNumberIndex.get(metric.id, clusteringNumber, internalIndices.head)

val oneInternalIndex = internalIndices.head

val first100ResultForMetricAndFirstInternalIndex =
  (0 until 100).map( i => extScores.internalsIndicesByMetricClusteringNumberIndex.get(metric.id, i, oneInternalIndex) )

first100ResultForMetricAndFirstInternalIndex
// extScores.internalsIndicesByMetricClusteringNumberIndex.get(metric.id, clusteringNumber, internalIndices.head)


entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total

internalIndices: Seq[org.clustering4ever.enums.InternalsIndices.Value] = ArrayBuffer(DaviesBouldin, BallHall)
extScores: org.clustering4ever.clustering.indices.ClustersIndicesAnalysisLocal[Long,org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.vectors.ScalarVector[scala.collection.mutable.ArrayBuffer[Double]],org.clustering4ever.clusterizables.EasyClusterizable,scala.collection.immutable.Vector] = ClustersIndicesAnalysisLocal(Vector(EasyClusterizable(0,Vectorizable(ScalarVector(ArrayBuffer(15.55, 28.65))),ScalarVector(ArrayBuffer(15.55, 28.65)),shapeless.HMap@6dd07060,Vector(3, 3, 2, 2, 0, 0, 2, 4, 0, 1, 4, 0, 5, 5, 1, 0, 2, 0, 0, 4, 5, 4, 6, 4, 5, 4, 5, 0, 4, 4, 4, 4, 4, 1, 7, 5, 3, 2, 5, 8, 8, 2, 2, 2, 0, 4, 7, 1, 0, 10, 3, 5, 1...

entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total

In [ ]:
val gt = Source.fromFile(groundTruePath).getLines.map(_.toInt).toVector
val everyExternalIndexes = ExternalsIndices.values.toSeq
indicesAnalysis.computeExternalsIndicesForEveryClusteringNumber(gt, everyExternalIndexes:_*)

entries total

## Define a new vectorization 

In [ ]:
def newVecto(v: ScalarVector[mutable.ArrayBuffer[Double]]) = new ScalarVector(v.vector.toVector)

def newVecto2(v: ScalarVector[mutable.ArrayBuffer[Double]]) = new ScalarVector(v.vector.tail)

val vectorizationNature = Scalar

val vectorization1 = EasyVectorizationLocal(1, Some(newVecto _))
val vectorization2 = EasyVectorizationLocal(2, Some(newVecto2 _))

// Add vectorization of another kind that current one
val cc3 = newCC.addVectorizationOnData(vectorization1)
// Add vectorization of same type that current one
val cc4 = cc3.addVectorizationOnData(vectorization2)
// Update current vector for same type that current one
val cc5 = cc4.switchToAnotherExistantVector(vectorization2)

(cc4.data.head.v, cc5.data.head.v)

(ScalarVector(ArrayBuffer(15.55, 28.65)),ScalarVector(ArrayBuffer(28.65)))

In [ ]:
// Update current vector for different type that current one
val cc6 = cc5.switchToAnotherExistantVector(vectorization1)
cc6.data.head.v

ScalarVector(Vector(15.55, 28.65))

In [ ]:
val metricVector = new Euclidean[Vector[Double]](false)


val generateAlgoForList = (23 to 30).map( i => KMeansArgs(i, metricVector, 0.0001, 50) ).map(_.obtainAlgorithm(cc6.data))

val cc7 = cc6.runAlgorithms(generateAlgoForList:_*)

In [ ]:
val cc8 = cc7.switchToAnotherExistantVector(vectorization2)

cc8.data.head.clusterIDs

entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total

## Show clustering associate to a specific vectorization

In [ ]:
cc8.vectorizations.get(vectorization1.vectorizationID)(vectorization1.vectoMapping).get.clusteringNumbers.toSeq.sorted

entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total

In [ ]:
cc8.vectorizations.get(firstVecto.vectorizationID)(firstVecto.vectoMapping).get.clusteringNumbers.toSeq.sorted

entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total 
 
 
 
 
 
 
 
 
 entries total